# Naive Bayes classifier

## Import package

In [1]:
from math import comb
from collections import Counter
import numpy as np

In [2]:
training_data_path = 'train-images.idx3-ubyte'
training_label_path = 'train-labels.idx1-ubyte'
testing_data_path = 't10k-images.idx3-ubyte'
testing_label_path = 't10k-labels.idx1-ubyte'

## Load Training Data

In [3]:
with open(training_data_path, mode = 'rb') as f:
    fileContent = f.read()

number_of_training_images = int.from_bytes(fileContent[4:8], 'big')
n = int.from_bytes(fileContent[8:12], 'big')
m = int.from_bytes(fileContent[12:16], 'big')

training_images = []
for i in range(number_of_training_images):
    training_images.append(fileContent[i * n * m + 16:(i + 1) * n * m + 16])
    
with open(training_label_path, mode = 'rb') as f:
    fileContent = f.read()
    
training_labels = []
for i in range(number_of_training_images):
    training_labels.append(fileContent[8 + i])

## discrete

In [4]:
count_freq = np.zeros((n * m, 10, 32))

for i, image in enumerate(training_images):
    for j, pixel in enumerate(image):
        count_freq[j][training_labels[i]][pixel >> 3] += 1
        
training_labels_counter = Counter(training_labels)

## continuous

In [5]:
mean = np.zeros((n * m, 10), dtype = float)
mean_square = np.zeros((n * m, 10), dtype = float)
sigma = np.zeros((n * m, 10), dtype = float)

for i, image in enumerate(training_images):
    for j, pixel in enumerate(image):
        mean[j][training_labels[i]] += pixel
        mean_square[j][training_labels[i]] += (pixel ** 2)

for i in range(n * m):
    for j in range(10):
        mean[i][j] /= training_labels_counter[j]
        mean_square[i][j] /= training_labels_counter[j]
        sigma[i][j] = mean_square[i][j] - mean[i][j] ** 2

## Load Testing Data

In [6]:
with open(testing_data_path, mode = 'rb') as f:
    fileContent = f.read()

number_of_testing_images = int.from_bytes(fileContent[4:8], 'big')

testing_images = []
for i in range(number_of_testing_images):
    testing_images.append(fileContent[i * n * m + 16:(i + 1) * n * m + 16])
    
with open(testing_label_path, mode = 'rb') as f:
    fileContent = f.read()
    
testing_labels = []
for i in range(number_of_testing_images):
    testing_labels.append(fileContent[8 + i])

## Toggle option

In [7]:
option = 1

## Result

In [8]:
error = 0

for i, image in enumerate(testing_images):
    prob = np.zeros(10)
    for label, count in training_labels_counter.items():
        prob[label] = np.log(count / number_of_training_images)

    for j, pixel in enumerate(image):
            
        for label in range(10):
            if option == 0:
                if count_freq[j][label][pixel >> 3] != 0:
                    prob[label] += np.log(count_freq[j][label][pixel >> 3] / sum(count_freq[j][label]))
                else:
                    # use 1 as a psuedocount
                    prob[label] += np.log(1 / sum(count_freq[j][label]))
            else:
                if sigma[j][label] != 0:
                    prob[label] += (-0.5 * np.log(2. * sigma[j][label] * np.pi))
                    prob[label] += (-((pixel - mean[j][label]) ** 2) / (2.0 * sigma[j][label]))
                    
    prob /= sum(prob)

    print('Posterior (in log scale):')
    for j in range(10):
        print(f'{j}: {prob[j]}')
    print(f'Prediction: {np.argmin(prob)}, Ans: {testing_labels[i]}\n')

    if np.argmin(prob) != testing_labels[i]:
        error += 1

print(f'error rate: {error / number_of_testing_images}')

Posterior (in log scale):
0: 0.005365168253118926
1: 0.1905701229306521
2: 0.007861725379850774
3: 0.0058498597496519705
4: 0.005202273180284201
5: 0.004620616309858214
6: 0.7671259485919133
7: 0.0034497136839210293
8: 0.006454508976957953
9: 0.003500062943791611
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.02053702739728638
1: 0.00849389434125798
2: 0.0016235445556556784
3: 0.3270266364130773
4: 0.008771554623516328
5: 0.004278287939771488
6: 0.004438352678797188
7: 0.42651981767919006
8: 0.013093075160257695
9: 0.18521780921119002
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 5.8448205743343864e-05
1: 3.840444978874954e-05
2: 5.609381267683223e-05
3: 5.362286167684947e-05
4: 5.413634167684727e-05
5: 5.440769193636236e-05
6: 5.212512485533849e-05
7: 0.9995190742895613
8: 5.1776976527454596e-05
9: 6.191024555684152e-05
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.044614971521878655
1: 0.4468148646238448
2: 0.05308877865584039
3: 0.05103895879751611
4: 0.05365251

Posterior (in log scale):
0: 5.957814740675039e-05
1: 0.00028412279354002936
2: 6.563645301196574e-05
3: 6.014043298171862e-05
4: 6.302385715432274e-05
5: 6.104132110119864e-05
6: 6.23427408605416e-05
7: 0.9992059361212664
8: 6.0031843259412955e-05
9: 7.814628941774069e-05
Prediction: 0, Ans: 5

Posterior (in log scale):
0: 0.0002002119661523848
1: 0.44213836399587303
2: 0.00017494912348218458
3: 0.5222323619039145
4: 0.00027881843747411164
5: 0.0007139577381676286
6: 0.0001497998763518357
7: 0.00481463249207044
8: 0.0004659895606233253
9: 0.028830914905890435
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.062005256208407473
1: 0.33994792850476757
2: 0.07214653365561241
3: 0.0651483406150283
4: 0.06696880325141719
5: 0.06621774622839265
6: 0.12838631934800876
7: 0.07372807638774832
8: 0.06237036592316851
9: 0.06308062987744896
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.05109080113882939
1: 0.5288317864483059
2: 0.052339627955285066
3: 0.04997811900656204
4: 0.04512682

Posterior (in log scale):
0: 0.04686045117967199
1: 0.36899335571140474
2: 0.027921958596104635
3: 0.02746553346025789
4: 0.027785278782745358
5: 0.02400527210364132
6: 0.02991121886630817
7: 0.01859348593679304
8: 0.4105248326525417
9: 0.01793861271053107
Prediction: 9, Ans: 7

Posterior (in log scale):
0: 0.009602065605746063
1: 0.026881480122907555
2: 0.009771610461244775
3: 0.009243293110725949
4: 0.008564133738724625
5: 0.00873618178039288
6: 0.013544957453932947
7: 0.8944903506480246
8: 0.008263500991638242
9: 0.010902426086662373
Prediction: 8, Ans: 8

Posterior (in log scale):
0: 0.02518400019694478
1: 0.7684154067480081
2: 0.02558962212425999
3: 0.024077829122194413
4: 0.021311913876457013
5: 0.02298777518182303
6: 0.03367580770986586
7: 0.03432810338732692
8: 0.022424388664627502
9: 0.022005152988492347
Prediction: 4, Ans: 4

Posterior (in log scale):
0: 0.02047764340374769
1: 0.37573836998043203
2: 0.026627602563160217
3: 0.02108480973081049
4: 0.019072244236746833
5: 0.0173

Posterior (in log scale):
0: 0.2363736628696177
1: 0.2939972240106215
2: 0.03223209945226852
3: 0.03162121608508553
4: 0.033329048157830964
5: 0.029323701434008656
6: 0.0359131830476676
7: 0.02234443458479955
8: 0.26429408886056077
9: 0.020571341497539208
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.012343045460021042
1: 0.020361700490978348
2: 0.011539345656023704
3: 0.010251279101060903
4: 0.009957612313719486
5: 0.010309890567939756
6: 0.8967563229547582
7: 0.009577630274963701
8: 0.009724155543025921
9: 0.009179017637508913
Prediction: 9, Ans: 7

Posterior (in log scale):
0: 0.0005582622437405063
1: 0.0005690669432019911
2: 0.0005450314689765969
3: 0.0005203340348897423
4: 0.0005076399383368604
5: 0.0005210271375633965
6: 0.0004868143662843106
7: 0.9952573753055376
8: 0.0004921814980316252
9: 0.0005422670634374863
Prediction: 6, Ans: 4

Posterior (in log scale):
0: 0.11211838684325692
1: 0.09581729954452699
2: 0.10628764405648068
3: 0.09822282453889972
4: 0.095928612607260

Posterior (in log scale):
0: 0.09818254289974306
1: 0.06301638561513496
2: 0.09255934995764338
3: 0.08853269099308579
4: 0.09037350952683328
5: 0.08966733919662355
6: 0.08532987652831381
7: 0.21897018705700266
8: 0.08499152105740025
9: 0.08837659716821912
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.05029996715336189
1: 0.3476559102743686
2: 0.0755550072169222
3: 0.05548651185838096
4: 0.0497949817878781
5: 0.04514748812176647
6: 0.2466130959849719
7: 0.03484179958466543
8: 0.061735195690249475
9: 0.032870042327434915
Prediction: 9, Ans: 7

Posterior (in log scale):
0: 0.1020118707462695
1: 0.07027400199830969
2: 0.10072387240505296
3: 0.09454924423924053
4: 0.09741949550107411
5: 0.09602843042732105
6: 0.09097946413925087
7: 0.15567722814151397
8: 0.09197001651671201
9: 0.1003663758852554
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.09475188210177386
1: 0.14538915093589908
2: 0.0929387410226263
3: 0.08655228389537573
4: 0.08346780862576164
5: 0.0849287942817211
6: 0.

...

Posterior (in log scale):
0: 0.09062302971984212
1: 0.0817427885330248
2: 0.0903672479695818
3: 0.08157475244326715
4: 0.08514374401555606
5: 0.08379408500634448
6: 0.23267250701318978
7: 0.09578643923298984
8: 0.07792241272473092
9: 0.08037299334147287
Prediction: 8, Ans: 2

Posterior (in log scale):
0: 0.0966693690557209
1: 0.09913567563583481
2: 0.09712178641826287
3: 0.08888345218525553
4: 0.08694315448551033
5: 0.08872433290808089
6: 0.16508272082944242
7: 0.11163090628148518
8: 0.08354363754163283
9: 0.08226496465877435
Prediction: 9, Ans: 8

Posterior (in log scale):
0: 0.11106810743334944
1: 0.07021875629957618
2: 0.10015117961397978
3: 0.096386632821234
4: 0.09748312937332936
5: 0.0974611684533883
6: 0.10378830395659812
7: 0.1381805578269956
8: 0.09013973027467943
9: 0.09512243394686982
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.06730675201153268
1: 0.065432621368706
2: 0.09402253268546355
3: 0.0813231059240962
4: 0.11438037048652663
5: 0.062360908611027714
6: 0.209

Posterior (in log scale):
0: 0.026856806919513195
1: 0.6972875747073592
2: 0.027426572718936792
3: 0.030312725223774303
4: 0.031139807983786835
5: 0.027874251962320268
6: 0.03403979318496461
7: 0.05541858615926337
8: 0.03107274222340188
9: 0.038571138916679605
Prediction: 0, Ans: 2

Posterior (in log scale):
0: 0.04098121858367063
1: 0.05896898671262265
2: 0.0692707699407157
3: 0.028478707024213287
4: 0.027485943895663577
5: 0.02876055364953776
6: 0.6688904543179118
7: 0.026272823427267205
8: 0.026457248393558903
9: 0.024433294054838454
Prediction: 9, Ans: 3

Posterior (in log scale):
0: 0.008982420446657481
1: 0.012367363861506012
2: 0.008982361100376236
3: 0.009350855968459663
4: 0.008333430630052593
5: 0.008721830844729264
6: 0.00899227888227898
7: 0.18566954197441082
8: 0.008287812705493282
9: 0.7403121035860357
Prediction: 8, Ans: 4

Posterior (in log scale):
0: 0.047606876734315205
1: 0.1323681365995872
2: 0.33130585408231233
3: 0.22283372938468973
4: 0.039421736349009834
5: 0.03

Posterior (in log scale):
0: 0.09227693161866728
1: 0.0683650953490162
2: 0.09147654592744894
3: 0.08264883282030726
4: 0.08651282922483
5: 0.08475475616324755
6: 0.21509281049824647
7: 0.11713207702938759
8: 0.07879792763206775
9: 0.08294219373678079
Prediction: 1, Ans: 8

Posterior (in log scale):
0: 0.016160102875685076
1: 0.5498435821853734
2: 0.024451567774266596
3: 0.018775555452733284
4: 0.016526875785173326
5: 0.015282501477873854
6: 0.3153183921740629
7: 0.012103745591264741
8: 0.01973196885000639
9: 0.011805707833560606
Prediction: 9, Ans: 7

Posterior (in log scale):
0: 0.05125702365157233
1: 0.05014427132485345
2: 0.08157333480868374
3: 0.03745738645663855
4: 0.03870287285842389
5: 0.03741449994898661
6: 0.5952467801497006
7: 0.03764381697149171
8: 0.035118760366717475
9: 0.03544125346293177
Prediction: 8, Ans: 8

Posterior (in log scale):
0: 0.00019698631865356617
1: 0.004794516067000716
2: 9.659208917889235e-05
3: 9.671111252377321e-05
4: 0.0014323198476732012
5: 0.000147

Posterior (in log scale):
0: 8.254667856470796e-05
1: 0.0009810715121745502
2: 9.593094410911917e-05
3: 9.782913315625166e-05
4: 0.0001644713463761944
5: 9.376280531222566e-05
6: 0.0003588098632181842
7: 0.9957068440817238
8: 9.18511099212755e-05
9: 0.002326882525443739
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.01695290364223201
1: 0.3552287448582353
2: 0.014488932901029188
3: 0.013752867002615021
4: 0.01881348670052717
5: 0.015689739003585636
6: 0.10604818385439067
7: 0.052813961117263046
8: 0.3742411861207874
9: 0.0319699947993346
Prediction: 3, Ans: 3

Posterior (in log scale):
0: 0.06341891237285263
1: 0.0040328665749067676
2: 0.00022538245750377102
3: 0.0005581882202836759
4: 0.010101202727784173
5: 0.0003169815141289334
6: 0.00018198962328572722
7: 0.8880216625315428
8: 0.004694322450951231
9: 0.028448491526760288
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.08053172816934229
1: 0.090353442621675
2: 0.08346113399200876
3: 0.07612021699222665
4: 0.095275170627

Posterior (in log scale):
0: 0.00033748432237401906
1: 0.00020792213302768984
2: 0.00030394684419758904
3: 0.0002946832894073169
4: 0.00030464465606337736
5: 0.0002981646720092549
6: 0.0002861475943515807
7: 0.9973577136180951
8: 0.0002788220214846144
9: 0.00033047084898957284
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.00025590979097866084
1: 0.0007063313514325475
2: 0.000221938403380853
3: 0.00022855398197297013
4: 0.0002860517582047951
5: 0.00023600488441260776
6: 0.00037249864295762277
7: 0.9970668473791777
8: 0.00021938725601788344
9: 0.00040647655146441413
Prediction: 8, Ans: 2

Posterior (in log scale):
0: 0.06061447908498539
1: 0.298265122373933
2: 0.06227697855076648
3: 0.05661097516121141
4: 0.07230839546438848
5: 0.06086024585659096
6: 0.06419911036777862
7: 0.1596469242750327
8: 0.05904664212085097
9: 0.10617112674446201
Prediction: 3, Ans: 3

Posterior (in log scale):
0: 0.033641244964908286
1: 0.06302755249090457
2: 0.043959850001671366
3: 0.024139025245150242
4

In [9]:
if option == 0:
    for i in range(10):
        print(f'{i}:')
        for pixel in range(n * m):
            if sum(count_freq[pixel][i][:16]) > sum(count_freq[pixel][i][16:]):
                print('0', end = ' ')
            else:
                print('1', end = ' ')
            if pixel % 28 == 27:
                print()
else:
    image = (mean >= 128) * 1
    for label in range(10):
        print(f'{label}:')
        for i in range(n):
            for j in range(m):
                print(image[i * m + j][label], end = ' ')
            print()
        print()
            

0:
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 1 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 0 0 0 0 0 

# Online Learning

## parameter

In [10]:
path = './testfile.txt'
a = 10
b = 1

## Load Data

In [11]:
with open(path, 'r') as f:
    cases = f.readlines()
    for i in range(len(cases)):
        cases[i] = cases[i].replace('\n', '')

In [12]:
for i, case in enumerate(cases):
    w, l = 0, 0
    for c in case:
        if c == '1':
            w += 1
        else:
            l += 1
    p = w / len(case)
    likelihood = comb(w + l, w) * (p ** w) * ((1 - p) ** l)
    print(f'case {i + 1}: {case}')
    print(f'Likelihood: {likelihood}')
    print(f'Beta prior:     a = {a}  b = {b}')
    a += w
    b += l
    print(f'Beta posterior: a = {a}  b = {b}\n')
    p = (a - 1) / (a + b - 2)

case 1: 0101010101001011010101
Likelihood: 0.16818809509277344
Beta prior:     a = 10  b = 1
Beta posterior: a = 21  b = 12

case 2: 0110101
Likelihood: 0.29375515303997485
Beta prior:     a = 21  b = 12
Beta posterior: a = 25  b = 15

case 3: 010110101101
Likelihood: 0.2286054241794335
Beta prior:     a = 25  b = 15
Beta posterior: a = 32  b = 20

case 4: 0101101011101011010
Likelihood: 0.18286870706509092
Beta prior:     a = 32  b = 20
Beta posterior: a = 43  b = 28

case 5: 111101100011110
Likelihood: 0.2143070548857833
Beta prior:     a = 43  b = 28
Beta posterior: a = 53  b = 33

case 6: 101110111000110
Likelihood: 0.20659760529408
Beta prior:     a = 53  b = 33
Beta posterior: a = 62  b = 39

case 7: 1010010111
Likelihood: 0.25082265600000003
Beta prior:     a = 62  b = 39
Beta posterior: a = 68  b = 43

case 8: 11101110110
Likelihood: 0.2619678932864457
Beta prior:     a = 68  b = 43
Beta posterior: a = 76  b = 46

case 9: 01000111101
Likelihood: 0.23609128871506807
Beta prior: 